In [1]:
from transformers import DataCollatorWithPadding,AutoModelForSequenceClassification, Trainer, TrainingArguments,AutoTokenizer,AutoModel,AutoConfig
from transformers import default_data_collator
from transformers import Wav2Vec2FeatureExtractor, HubertForSequenceClassification
import torch
import torch.nn as nn
from datasets import Dataset, Audio, Value, Features,load_dataset,ClassLabel
from transformers import Wav2Vec2Processor
from transformers.modeling_outputs import SequenceClassifierOutput
import numpy as np
from transformers import AdamW,get_scheduler
from datasets import load_metric
from tqdm.auto import tqdm
import os
from torch.utils.data import DataLoader
from datasets import load_metric


def featurize(batch):
#     audio_arrays = [batch['audio'][i]['array'] for i in range(len(batch))]
    audio_arrays = [batch['audio'][i]['array'] for i in range(len(batch['id']))]
#     print(len(audio_arrays))
    inputs = feature_extractor(
        audio_arrays, 
        sampling_rate=16_000, 
        max_length=int(16_000 * 5),  # 10s
        truncation=True, 
        padding='max_length',
    )
    return inputs


checkpoint = "facebook/wav2vec2-base"
weighted_sum = False
# checkpoint = "facebook/hubert-base-ls960"
# checkpoint = "facebook/wav2vec2-large-lv60"

x = [str(i) for i in range(0,100,1)]
features = Features(
    {
        "id": Value("string"),
        "speaker_id": Value("string"), 
        'path': Value('string'),
        "audio": Audio(sampling_rate=16000),
        "label": ClassLabel(num_classes=100,names=x,names_file=None,id=None)
    }
)


dataset = load_dataset('csv', 
                       data_files={'test': 'test_100.csv'},
                       features=features)
dataset = dataset.map(remove_columns=(['path','speaker_id']),num_proc=24)
dataset = dataset.sort("label")
# sampling_rate = dataset.features["audio"].sampling_rate
if 'base' in checkpoint and not weighted_sum:
    feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained(checkpoint,return_attention_mask=False)
else:
    feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained(checkpoint,return_attention_mask=True)


dataset = dataset.map(featurize, remove_columns='audio',batched=True,num_proc=20,batch_size=1)

# dataset = dataset.rename_column('id','label_ids')

if 'base' in checkpoint and not weighted_sum:
    dataset.set_format("torch",columns=["id","input_values", "label"])
else:
    dataset.set_format("torch",columns=["id","input_values", "attention_mask", "label"])

2022-11-27 20:04:22.723144: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2022-11-27 20:04:22.729051: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/torque/current/lib::
2022-11-27 20:04:22.729068: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
Using custom data configuration default-b0c48fcb8e795d32
Found cached dataset csv (/storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317)


  0%|          | 0/1 [00:00<?, ?it/s]

Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-3abca03ae629d64d.arrow


Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-5439afa02ec42459.arrow


Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-45b7b43d1b8be568.arrow


...

Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-5b60f4f1df9f3314.arrow


Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-24987004d549abaf.arrow


Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-e668e9ebb27359cd.arrow


Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-0ceddb92ff813327.arrow


Loading cached processed dataset at /storage/home/hcocice1/hbharadwaj6/.cache/huggingface/datasets/csv/default-b0c48fcb8e795d32/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-eca874051bc7c686.arrow


### Model

In [2]:
class CustomBaseSID(nn.Module):
    def __init__(self,checkpoint,num_labels,inter_layer_num,attend):
        
        ### attend is a boolean
        super(CustomBaseSID, self).__init__()
#         self.hubert = HubertForSequenceClassification.from_pretrained("superb/hubert-base-superb-sid")
        self.model =AutoModel.from_pretrained(checkpoint,config=AutoConfig.from_pretrained(checkpoint, output_attentions=attend,output_hidden_states=True))
        self.num_labels = num_labels
        self.attend_mask = attend
        ### New layers:
        self.linear1 = nn.Linear(768, 1024)
        self.linear2 = nn.Linear(1024, num_labels)
        
        ### Intermediate Layer Number
        self.layer_num = inter_layer_num

    def forward(self, input_values=None, attention_mask=None,labels=None):
        if(self.attend_mask):
            outputs = self.model(input_values=input_values, attention_mask=attention_mask)
        else:
            outputs = self.model(input_values=input_values, attention_mask=None)
        feature = outputs.hidden_states[self.layer_num-1]
        agg_vec_list = []
        for i in range(len(feature)):
            if(attention_mask==None):
                length = len(feature[i])
            
            else:
                if torch.nonzero(attention_mask[i] < 0, as_tuple=False).size(0) == 0:
                    length = len(feature[i])
                else:
                    length = torch.nonzero(attention_mask[i] < 0, as_tuple=False)[0] + 1
            agg_vec=torch.mean(feature[i][:length], dim=0)
            agg_vec_list.append(agg_vec)
        mean = torch.stack(agg_vec_list)
        # sequence_output has the following shape: (batch_size, sequence_length, 768)
        linear1_output = self.linear1(mean) ## extract the 1st token's embeddings
        logits = self.linear2(linear1_output)
        
        loss = None
        if labels is not None:
            loss_fct = nn.CrossEntropyLoss()
            loss = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))

        return SequenceClassifierOutput(loss=loss, logits=logits, hidden_states=outputs.hidden_states,attentions=outputs.attentions)


In [3]:
def freeze_layers_transformer(model_ft,keywords,inter_layer,encoder_mode=True):
    ct = 0
    for child in model_ft.children():
        for name,param in child.named_parameters():
            if(encoder_mode):
                if 'encoder' in name and str(ct) in name:
                    ct += 1
                    if ct < inter_layer:
                        param.requires_grad = False
                    
            for word in keywords:         
                if word in name:
                    param.requires_grad = False
                            
    return model_ft

In [4]:
dataset

DatasetDict({
    test: Dataset({
        features: ['id', 'label', 'input_values'],
        num_rows: 632
    })
})

In [5]:
def load_model(checkpoint, num_labels, inter_layer, model_dirpath, device):
    dirpath = model_dirpath + str(inter_layer)+'/'
    PATH = dirpath+str(4)+'.pt'
    if 'base' in checkpoint:
        attend = False
#     model_name = "model_ft_" + pretrained_model_name + str(inter_layer)
    model_ft = CustomBaseSID(checkpoint=checkpoint,num_labels=100,inter_layer_num=inter_layer,attend=attend)
    model_ft.load_state_dict(torch.load(PATH, map_location=device))

    return model_ft

In [6]:
metric_name="accuracy"
metric = load_metric(metric_name)
test_dataloader = DataLoader(dataset["test"], batch_size=1, collate_fn=default_data_collator)

/scratch/470888.sched-coc-ice.pace.gatech.edu/ipykernel_99554/1426700558.py:2: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric(metric_name)


In [7]:
# inter_layer = 12
# dirpath="/storage/home/hcocice1/hbharadwaj6/StatML/Final_Project/code/w2v-base/"+str(inter_layer)+'/'
# PATH = dirpath+str(4)+'.pt'
# checkpoint = "facebook/wav2vec2-base"

# if 'base' in checkpoint:
#     attend = False

# device = "cpu"

# model_w2vbase_12 = CustomBaseSID(checkpoint=checkpoint,num_labels=100,inter_layer_num=inter_layer,attend=attend)
# #torch.save(model_ft.state_dict(), PATH)
# model_w2vbase_12.load_state_dict(torch.load(PATH, map_location=device))

# metric_name="accuracy"
# metric = load_metric(metric_name)
# test_dataloader = DataLoader(dataset["test"], batch_size=1, collate_fn=default_data_collator)


In [8]:
# keys = list(dataset['test'].features.keys())
keys = list(dataset['test']['id'])
test_dict = dict.fromkeys(keys)

In [9]:
list(test_dict.keys())[0]

'id10001-Y8hIVOBuels-00001'

In [10]:
def evaluate(test_dataloader,model_ft):
    test_dict = dict.fromkeys(list(dataset['test']['id']))
    keys = list(test_dict.keys())
    
    for i,batch in enumerate(test_dataloader):
        batch = {k: v.to(device) for k, v in batch.items()}
        with torch.no_grad():
            outputs = model_ft(**batch)
        logits = outputs.logits
        sm = torch.nn.Softmax(dim=1)
        probabilities = sm(logits)
        test_dict[keys[i]] = dict.fromkeys(['labels','probabilities','predictions'])
        test_dict[keys[i]]['labels'] = batch['labels'].detach().numpy()
        test_dict[keys[i]]['probabilities'] = probabilities[0].detach().numpy()
        predictions = torch.argmax(logits, dim=-1)
        test_dict[keys[i]]['predictions'] = predictions[0].detach().numpy()
        metric.add_batch(predictions=predictions, references=batch["labels"])
    accuracy = metric.compute()
    return test_dict,accuracy

## w2vbase 12 layer

In [11]:
checkpoint_w2vbase = 'facebook/wav2vec2-base'
model_dirpath = "/storage/home/hcocice1/hbharadwaj6/StatML/Final_Project/code/w2v-base/"
device = "cpu"
model_ft_w2vbase_12 = load_model(checkpoint_w2vbase, 100, 12, model_dirpath, device)

w2vbase_12,w2vbase_12_accuracy = evaluate(test_dataloader,model_ft_w2vbase_12)

/storage/home/hcocice1/hbharadwaj6/.conda/envs/ece6254/lib/python3.8/site-packages/transformers/configuration_utils.py:369: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(
Some weights of the model checkpoint at facebook/wav2vec2-base were not used when initializing Wav2Vec2Model: ['quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_q.bias', 'project_hid.bias', 'project_q.weight', 'project_hid.weight', 'quantizer.weight_proj.weight']
- This IS expected if you are initializing Wav2Vec2Model from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2Model fro

## w2vbase 9 layer

In [12]:
checkpoint_w2vbase = 'facebook/wav2vec2-base'
model_dirpath = "/storage/home/hcocice1/hbharadwaj6/StatML/Final_Project/code/w2v-base/"
model_ft_w2vbase_9 = load_model(checkpoint_w2vbase, 100, 9, model_dirpath, device)

w2vbase_9,w2vbase_9_accuracy = evaluate(test_dataloader,model_ft_w2vbase_9)

/storage/home/hcocice1/hbharadwaj6/.conda/envs/ece6254/lib/python3.8/site-packages/transformers/configuration_utils.py:369: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(
Some weights of the model checkpoint at facebook/wav2vec2-base were not used when initializing Wav2Vec2Model: ['quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_q.bias', 'project_hid.bias', 'project_q.weight', 'project_hid.weight', 'quantizer.weight_proj.weight']
- This IS expected if you are initializing Wav2Vec2Model from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2Model fro

## w2vbase 6 layer

In [13]:
checkpoint_w2vbase = 'facebook/wav2vec2-base'
model_dirpath = "/storage/home/hcocice1/hbharadwaj6/StatML/Final_Project/code/w2v-base/"
model_ft_w2vbase_6 = load_model(checkpoint_w2vbase, 100, 6, model_dirpath, device)

w2vbase_6,w2vbase_6_accuracy = evaluate(test_dataloader,model_ft_w2vbase_12)

/storage/home/hcocice1/hbharadwaj6/.conda/envs/ece6254/lib/python3.8/site-packages/transformers/configuration_utils.py:369: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(
Some weights of the model checkpoint at facebook/wav2vec2-base were not used when initializing Wav2Vec2Model: ['quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_q.bias', 'project_hid.bias', 'project_q.weight', 'project_hid.weight', 'quantizer.weight_proj.weight']
- This IS expected if you are initializing Wav2Vec2Model from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2Model fro

## w2vbase results

### 12 layer

In [14]:
w2vbase_12

{'id10001-Y8hIVOBuels-00001': {'labels': array([0]),
  'probabilities': array([4.45755661e-01, 4.50112821e-05, 2.90368829e-04, 9.00884042e-04,
         1.14312302e-02, 3.61146609e-04, 7.43848723e-05, 1.13714023e-05,
         4.07069139e-02, 1.18542695e-03, 5.18775079e-04, 1.31751785e-05,
         2.08679019e-04, 2.28005829e-05, 7.53142929e-04, 2.63748334e-05,
         2.02834162e-05, 2.37838045e-04, 6.23098749e-05, 1.72214641e-03,
         1.03216607e-03, 3.07804476e-05, 2.35084939e-04, 1.58577133e-03,
         1.08644917e-05, 3.18768522e-04, 1.52227515e-03, 6.81518140e-05,
         3.77432036e-04, 1.15007766e-04, 6.41720660e-04, 4.40659460e-05,
         5.48377924e-04, 4.96769326e-06, 1.36757782e-03, 1.15990399e-04,
         7.19789881e-04, 1.48205509e-04, 2.21793343e-05, 1.24634726e-05,
         5.88950119e-04, 4.00350109e-04, 5.25108262e-05, 8.06383614e-05,
         4.77992035e-05, 2.89378186e-05, 6.98062504e-05, 3.06761387e-04,
         6.34398612e-06, 1.20794422e-04, 3.75374249e-0

In [15]:
w2vbase_12_accuracy

{'accuracy': 0.8734177215189873}

### 9 layer

In [16]:
w2vbase_9

{'id10001-Y8hIVOBuels-00001': {'labels': array([0]),
  'probabilities': array([3.4170038e-01, 1.1318372e-04, 8.2522811e-06, 1.2032461e-02,
         1.1078305e-02, 1.3071452e-03, 4.7747721e-04, 7.5157667e-03,
         2.8067956e-02, 4.3253959e-03, 5.0552655e-05, 2.1431455e-04,
         2.1886786e-03, 2.8771967e-05, 1.5483206e-04, 1.5484425e-04,
         1.4814735e-05, 1.5603728e-04, 3.1242635e-05, 3.4207432e-04,
         5.4922290e-05, 3.2346093e-04, 7.0080138e-04, 2.0609594e-04,
         3.0656590e-04, 5.0496282e-03, 1.8316293e-04, 4.4405102e-04,
         2.6996111e-04, 4.0449360e-03, 5.3476979e-04, 4.7389429e-05,
         3.8389175e-05, 2.2774355e-03, 3.7716325e-02, 2.3984141e-05,
         1.4024231e-04, 4.5836918e-04, 3.4220368e-03, 9.0069581e-05,
         1.6479076e-05, 2.5464624e-05, 2.3569229e-04, 1.8428797e-04,
         3.1224230e-05, 1.9478804e-04, 5.1641040e-05, 3.3569243e-04,
         1.4136286e-04, 7.4310636e-04, 3.6585139e-04, 5.1827636e-04,
         1.8516335e-05, 1.5720674

In [17]:
w2vbase_9_accuracy

{'accuracy': 0.8813291139240507}

### 6 layer

In [18]:
w2vbase_6

{'id10001-Y8hIVOBuels-00001': {'labels': array([0]),
  'probabilities': array([4.45755661e-01, 4.50112821e-05, 2.90368829e-04, 9.00884042e-04,
         1.14312302e-02, 3.61146609e-04, 7.43848723e-05, 1.13714023e-05,
         4.07069139e-02, 1.18542695e-03, 5.18775079e-04, 1.31751785e-05,
         2.08679019e-04, 2.28005829e-05, 7.53142929e-04, 2.63748334e-05,
         2.02834162e-05, 2.37838045e-04, 6.23098749e-05, 1.72214641e-03,
         1.03216607e-03, 3.07804476e-05, 2.35084939e-04, 1.58577133e-03,
         1.08644917e-05, 3.18768522e-04, 1.52227515e-03, 6.81518140e-05,
         3.77432036e-04, 1.15007766e-04, 6.41720660e-04, 4.40659460e-05,
         5.48377924e-04, 4.96769326e-06, 1.36757782e-03, 1.15990399e-04,
         7.19789881e-04, 1.48205509e-04, 2.21793343e-05, 1.24634726e-05,
         5.88950119e-04, 4.00350109e-04, 5.25108262e-05, 8.06383614e-05,
         4.77992035e-05, 2.89378186e-05, 6.98062504e-05, 3.06761387e-04,
         6.34398612e-06, 1.20794422e-04, 3.75374249e-0

In [19]:
w2vbase_6_accuracy

{'accuracy': 0.8734177215189873}

## w2vbase ensemble

In [20]:
num_models = 3
ensemble_test_dict = w2vbase_6.copy()
key = 'id10001-Y8hIVOBuels-00001'

for key in w2vbase_6.keys():
    mean_prob = np.asarray([sum(x) for x in zip(w2vbase_6[key]['probabilities'], w2vbase_9[key]['probabilities'], w2vbase_12[key]['probabilities'])])/num_models
    ensemble_test_dict[key]['probabilities'] = mean_prob
    ensemble_test_dict[key]['predictions'] = np.argmax(mean_prob)
    metric.add(prediction=ensemble_test_dict[key]['predictions'], reference = ensemble_test_dict[key]['labels'])

accuracy = metric.compute()

In [21]:
accuracy

{'accuracy': 0.9145569620253164}

## Top 3 Probabilities

In [27]:
def get_top3_accuracy(out_dict):
    test_length = 632
    correct_count=0
    for key in out_dict.keys():
        val=out_dict[key]
        out_dict[key]['top3'] = []
        top_3_out_dict=sorted(zip(val['probabilities'],range(len(val['probabilities']))), reverse = True)[:3]
        out_dict[key]['top3'] = top_3_out_dict
    for key in out_dict.keys():
        top3_labels = [x[1] for x in out_dict[key]['top3']]
        label = out_dict[key]['labels'][0]
        if (label in top3_labels):
            correct_count+=1
            
    return out_dict,correct_count/test_length


# w2vbase_12,top3_w2vbase_12_acc = get_top3_accuracy(w2vbase_12)
# w2vbase_9,top3_w2vbase_9_acc = get_top3_accuracy(w2vbase_9)
# w2vbase_6,top3_w2vbase_6_acc = get_top3_accuracy(w2vbase_6)
ensemble_test_dict_top3, ensemble_acc_top3 = get_top3_accuracy(ensemble_test_dict)

In [38]:
ensemble_test_dict_top3

{'id10001-Y8hIVOBuels-00001': {'labels': array([0]),
  'probabilities': array([4.11070565e-01, 6.77354280e-05, 1.96329980e-04, 4.61140981e-03,
         1.13135884e-02, 6.76479482e-04, 2.08748985e-04, 2.51283649e-03,
         3.64939279e-02, 2.23208327e-03, 3.62700938e-04, 8.02216370e-05,
         8.68678879e-04, 2.47910442e-05, 5.53705972e-04, 6.91979731e-05,
         1.84605224e-05, 2.10571122e-04, 5.19541281e-05, 1.26212238e-03,
         7.06418141e-04, 1.28340609e-04, 3.90323752e-04, 1.12587953e-03,
         1.09431627e-04, 1.89572175e-03, 1.07590441e-03, 1.93451551e-04,
         3.41608393e-04, 1.42498386e-03, 6.06070370e-04, 4.51737736e-05,
         3.78381674e-04, 7.62456963e-04, 1.34838270e-02, 8.53216461e-05,
         5.26607357e-04, 2.51593398e-04, 1.15546515e-03, 3.83321755e-05,
         3.98126438e-04, 2.75388281e-04, 1.13571315e-04, 1.15188232e-04,
         4.22742123e-05, 8.42212248e-05, 6.37511803e-05, 3.16405067e-04,
         5.13502785e-05, 3.28231734e-04, 3.72199963e-0

In [79]:
top3_for_mistakes = []

for key in ensemble_test_dict_top3.keys():
    if(ensemble_test_dict_top3[key]['predictions'] != ensemble_test_dict_top3[key]['labels']):
        top3_for_mistakes.append((key, ensemble_test_dict_top3[key]))
        
top3_for_mistakes

[('id10001-Y8hIVOBuels-00002',
  {'labels': array([0]),
   'probabilities': array([3.76618276e-01, 8.02361562e-05, 3.42644381e-04, 2.81778288e-03,
          5.32768779e-03, 2.29628262e-04, 1.26049073e-04, 3.75731001e-04,
          7.06102777e-02, 1.44939629e-03, 4.68253164e-04, 3.50358423e-05,
          2.55706186e-04, 2.73162107e-05, 8.90656011e-04, 1.02229224e-04,
          3.25228208e-05, 2.11954088e-04, 1.02703141e-04, 2.98981485e-03,
          8.57734922e-04, 1.23188028e-04, 3.35681126e-04, 1.38028141e-03,
          3.47604376e-05, 3.12078152e-04, 1.14167764e-03, 1.42606693e-04,
          3.08728680e-04, 2.41753999e-04, 8.76668065e-04, 3.79041303e-05,
          5.92853439e-04, 1.06930394e-04, 1.04345558e-03, 1.18561285e-04,
          3.59311872e-04, 1.06536170e-04, 3.37583973e-04, 2.86645979e-05,
          2.73364730e-04, 9.96225982e-04, 9.87627403e-05, 8.94490877e-05,
          6.67422200e-05, 5.90587297e-05, 1.04659674e-04, 1.61610808e-04,
          2.06762882e-05, 1.85479177e-0

In [89]:
label_probs = []

for i in range(len(top3_for_mistakes)):
    label_probs.append((top3_for_mistakes[i][0],top3_for_mistakes[i][1]['probabilities'][top3_for_mistakes[i][1]['labels']], top3_for_mistakes[i][1]['labels']))
label_probs.sort(key = lambda label_probs: label_probs[1])

label_probs[0:5]

[('id10029-ycz4HbK8diE-00005', array([0.00384342]), array([28])),
 ('id10084-qWm2A410eUY-00006', array([0.00659589]), array([83])),
 ('id10065-Q26FFVLMNaw-00001', array([0.01069428]), array([64])),
 ('id10035-HGc7QkB_ysk-00005', array([0.01273815]), array([34])),
 ('id10065-Q26FFVLMNaw-00003', array([0.0335597]), array([64]))]

In [88]:
final_mistakes = []
for label in label_probs[0:5]:
    for mistake in top3_for_mistakes:
        if(mistake[0] is label[0]):
            final_mistakes.append(mistake[1])

final_mistakes

[{'labels': array([28]),
  'probabilities': array([3.89570545e-04, 3.79780128e-04, 1.59731072e-04, 3.77951345e-04,
         1.34625666e-03, 4.22971595e-05, 6.31773883e-04, 4.39990915e-05,
         9.89277661e-03, 6.69409828e-02, 1.83700981e-02, 1.08511299e-04,
         4.63284960e-04, 8.35038845e-05, 1.41487653e-03, 2.84689595e-04,
         2.66111619e-03, 3.32170757e-05, 5.32176897e-03, 1.94477694e-04,
         4.22920290e-04, 2.17323798e-04, 1.42501111e-01, 8.06175677e-04,
         1.42078921e-02, 2.33707232e-04, 6.51256201e-04, 3.60974477e-03,
         3.84341648e-03, 8.65134158e-05, 2.95369255e-04, 1.28495791e-04,
         7.94595933e-04, 8.33269466e-05, 1.92643068e-05, 2.53577879e-04,
         1.51792644e-04, 3.14627062e-05, 1.10470481e-04, 2.68674570e-04,
         1.14102353e-05, 1.69045703e-01, 4.09049996e-04, 8.62821707e-06,
         3.99304718e-05, 3.00004792e-04, 3.78636165e-05, 7.14613755e-06,
         4.85206681e-03, 5.16707753e-04, 5.20426544e-02, 1.42951455e-05,
         

In [ ]:
lens=['worst1', 'worst2', 'worst3', 'worst4', 'worst5']
width = 0.2
fig = plt.figure(figsize = (10, 5))

# Set position of bar on X axis
br1 = np.arange(5)
br2 = [x + width for x in br1]
br3 = [x + width for x in br2]

# creating the bar plot
plt.bar(br1, list_6, color ='r', width = width,
        edgecolor ='grey', label ='1st')
plt.bar(br2, list_9, color ='g', width = width,
        edgecolor ='grey', label ='2nd')
plt.bar(br3, list_12, color ='b', width = width,
        edgecolor ='grey', label ='3rd')
 
plt.xlabel("Worst classified audios")
plt.ylabel("Probability")
plt.xticks([r + width for r in range(len(list_6))],lens)
plt.title("Accuracy for different audio lengths")
plt.legend()
plt.show()
br1,br2,br3